In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
# System imports
import os
import sys
import yaml

# External imports
import matplotlib.pyplot as plt
import scipy as sp
from sklearn.metrics import auc
import numpy as np
import pandas as pd
import seaborn as sns
import torch
from pytorch_lightning.loggers import TensorBoardLogger, WandbLogger
from pytorch_lightning.callbacks import GradientAccumulationScheduler
from pytorch_lightning import Trainer
import wandb
import math
sys.path.append('../..')

from LightningModules.ObjectCondensation.Models.models import DualHierarchicalGNN, HierarchicalGNN

device = "cuda" if torch.cuda.is_available() else "cpu"
from pytorch_lightning.callbacks import ModelCheckpoint

In [3]:
def kaiming_init(model):
    for name, param in model.named_parameters():
        try:
            if name.endswith(".bias"):
                param.data.fill_(0)
            elif name.startswith("layers.0"):  # The first layer does not have ReLU applied on its input
                param.data.normal_(0, 1 / math.sqrt(param.shape[1]))
            else:
                param.data.normal_(0, math.sqrt(2) / math.sqrt(param.shape[1]))
        except:
            continue

In [4]:
def load_from_pretrained(model, path):
    
    checkpoint = torch.load(path)
    state_dict = checkpoint["state_dict"]
    model.load_state_dict(state_dict, strict=False)
    del state_dict
    
    return model

## Construct PyLightning model

In [5]:
with open("object_condensation_default.yaml") as f:
    hparams = yaml.load(f, Loader=yaml.FullLoader)

In [6]:
if hparams["use_toy"]:
    hparams["regime"] = []
    hparams["spatial_channels"] = 2

model = DualHierarchicalGNN(hparams)
model_path = "/global/cfs/cdirs/m3443/usr/ryanliu/ITk_object_condensation/ITk_object_condensation/28pvelhb/checkpoints/last.ckpt"

if hparams["use_pretrain"]:
    model = load_from_pretrained(model, model_path)
else:
    kaiming_init(model)

## Metric Learning

In [7]:
from pytorch_lightning.callbacks import ModelCheckpoint

checkpoint_callback = ModelCheckpoint(
    monitor='track_eff',
    mode="max",
    save_top_k=2,
    save_last=True)

In [ ]:
logger = WandbLogger(project="ITk_object_condensation")
accumulator = GradientAccumulationScheduler(scheduling={0: 1, 4: 2, 8: 4})
trainer = Trainer(gpus=1, max_epochs=hparams["max_epochs"], gradient_clip_val=0.5, logger=logger, num_sanity_val_steps=2, callbacks=[checkpoint_callback], log_every_n_steps = 50, default_root_dir="/global/cfs/cdirs/m3443/usr/ryanliu/ITk_object_condensation/")
trainer.fit(model)

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: liuryan30 (exatrkx). Use `wandb login --relogin` to force relogin


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

   | Name                    | Type                     | Params
----------------------------------------------------------------------
0  | node_encoder            | Sequential               | 100 K 
1  | edge_encoder            | Sequential               | 101 K 
2  | second_node_encoder     | Sequential               | 100 K 
3  | second_edge_encoder     | Sequential               | 101 K 
4  | bipartite_edge_scoring  | Sequential               | 265 K 
5  | supergraph_construction | HierarchicalGNNAttention | 535 K 
6  | ignn_embedding_blocks   | ModuleList               | 2.9 M 
7  | ignn_encoding_blocks    | ModuleList               | 2.2 M 
8  | hgnn_blocks             | ModuleList               | 6.4 M 
9  | output_layer            | Sequential               | 232 K 
10 | softmax              

Sanity Checking: 0it [00:00, ?it/s]

/global/homes/r/ryanliu/.conda/envs/rapids/lib/python3.8/site-packages/torch_geometric/deprecation.py:12: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)
/global/homes/r/ryanliu/.conda/envs/rapids/lib/python3.8/site-packages/torch/utils/checkpoint.py:25: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn("None of the inputs have requires_grad=True. Gradients will be None")


Label prop iterations: 19
Label prop iterations: 9
Label prop iterations: 8
Label prop iterations: 7
Label prop iterations: 6
Label prop iterations: 3
Label prop iterations: 2
Iterations: 7
13797,271,413,35,447,2067
Label prop iterations: 5
Label prop iterations: 4
Label prop iterations: 2
Iterations: 3
636,127,218,14,182,502
Label prop iterations: 2
Iterations: 1
625,68,102,8,69,133


...

Label prop iterations: 13
Label prop iterations: 4
Label prop iterations: 4
Iterations: 3
847,128,212,23,196,776
Label prop iterations: 8
Label prop iterations: 10
Label prop iterations: 6
Label prop iterations: 5
Label prop iterations: 4
Iterations: 5
686,162,281,18,300,1174
Label prop iterations: 4
Label prop iterations: 2
Iterations: 2
646,88,144,9,119,291
Label prop iterations: 14
Label prop iterations: 6
Label prop iterations: 3
Iterations: 3
546,95,130,13,155,751
Label prop iterations: 10
Label prop iterations: 8
Label prop iterations: 6
Label prop iterations: 5
Label prop iterations: 3
Iterations: 5
474,135,180,18,262,1039
Label prop iterations: 5
Label prop iterations: 2
Iterations: 2
403,67,92,9,102,266
Label prop iterations: 13
Label prop iterations: 5
Label prop iterations: 3
Iterations: 3
580,105,124,17,179,611
Label prop iterations: 8
Label prop iterations: 7
Label prop iterations: 7
Label prop iterations: 5
Label prop iterations: 3
Iterations: 5
485,149,172,22,282,839
Lab

Validation: 0it [00:00, ?it/s]

Label prop iterations: 12
Label prop iterations: 6
Label prop iterations: 3
Label prop iterations: 2
Iterations: 4
820,165,263,21,268,965
Label prop iterations: 8
Label prop iterations: 6
Label prop iterations: 7
Label prop iterations: 4
Label prop iterations: 2
Iterations: 5
676,175,290,18,311,1086
Label prop iterations: 3
Label prop iterations: 2
Iterations: 2
586,88,145,9,128,268
Label prop iterations: 13
Label prop iterations: 6
Label prop iterations: 3
Iterations: 3
574,113,124,18,185,669
Label prop iterations: 7
Label prop iterations: 7
Label prop iterations: 7
Label prop iterations: 5
Label prop iterations: 2
Iterations: 5
475,154,167,24,284,871
Label prop iterations: 5
Label prop iterations: 2
Iterations: 2
434,77,83,12,115,253
Label prop iterations: 14
Label prop iterations: 5
Label prop iterations: 3
Iterations: 3
588,110,127,18,182,645
Label prop iterations: 7
Label prop iterations: 10
Label prop iterations: 8
Label prop iterations: 6
Label prop iterations: 2
Iterations: 5
5

Validation: 0it [00:00, ?it/s]

Label prop iterations: 13
Label prop iterations: 5
Label prop iterations: 3
Iterations: 3
907,131,214,17,208,826
Label prop iterations: 8
Label prop iterations: 7
Label prop iterations: 7
Label prop iterations: 4
Iterations: 4
699,137,234,15,251,1013
Label prop iterations: 4
Label prop iterations: 2
Iterations: 2
589,227,142,9,122,540
Label prop iterations: 13
Label prop iterations: 6
Label prop iterations: 3
Iterations: 3
516,90,116,13,154,641
Label prop iterations: 7
Label prop iterations: 8
Label prop iterations: 6
Label prop iterations: 4
Label prop iterations: 2
Iterations: 5
440,129,156,18,256,750
Label prop iterations: 3
Label prop iterations: 2
Iterations: 2
383,76,80,9,125,176
Label prop iterations: 13
Label prop iterations: 5
Label prop iterations: 3
Label prop iterations: 2
Iterations: 4
570,111,149,14,189,948
Label prop iterations: 8
Label prop iterations: 8
Label prop iterations: 6
Label prop iterations: 4
Label prop iterations: 3
Iterations: 5
420,123,162,14,248,843
Label

In [ ]:
training_id = input()
model_path = "/global/cfs/cdirs/m3443/usr/ryanliu/ITk_object_condensation/ITk_object_condensation/{}/checkpoints/last.ckpt".format(training_id)
model = HierarchicalGNN.load_from_checkpoint(model_path)
    
logger = WandbLogger(project="ITk_object_condensation", id = training_id)
accumulator = GradientAccumulationScheduler(scheduling={0: 1, 4: 2, 8: 4})
trainer = Trainer(gpus=1, max_epochs=hparams["max_epochs"], logger=logger, num_sanity_val_steps=2, callbacks=[checkpoint_callback, accumulator], log_every_n_steps = 50, default_root_dir="/global/cfs/cdirs/m3443/usr/ryanliu/ITk_object_condensation/")
trainer.fit(model, ckpt_path="/global/cfs/cdirs/m3443/usr/ryanliu/ITk_object_condensation/ITk_object_condensation/{}/checkpoints/last.ckpt".format(training_id))

## Sweep

In [5]:
run_name = input()

 track_len


In [6]:
with open("object_condensation_sweep.yaml") as f:
        sweep_hparams = yaml.load(f, Loader=yaml.FullLoader)
with open("object_condensation_default.yaml") as f:
        default_hparams = yaml.load(f, Loader=yaml.FullLoader)   

In [7]:
sweep_configuration = {
    "name": run_name,
    "project": "ITk_object_condensation",
    "metric": {"name": "track_eff", "goal": "maximize"},
    "method": "grid",
    "parameters": sweep_hparams
}

In [8]:
def training():
    wandb.init()
    hparams = {**default_hparams, **wandb.config}
    if hparams["use_toy"]:
        hparams["regime"] = []
        hparams["spatial_channels"] = 2
        
    model = DualHierarchicalGNN(hparams)
    
    if hparams["use_pretrain"]:
        model = load_from_pretrained(model, model_path)
    
    checkpoint_callback = ModelCheckpoint(
        monitor='track_eff',
        mode="max",
        save_top_k=2,
        save_last=True)
    
    kaiming_init(model)

    logger = WandbLogger()
    trainer = Trainer(gpus=1, max_epochs=default_hparams["max_epochs"], log_every_n_steps = 50, logger=logger, callbacks=[checkpoint_callback], default_root_dir="/global/cfs/cdirs/m3443/usr/ryanliu/ITk_barrel_embedding/")
    trainer.fit(model)

In [ ]:
sweep_id = wandb.sweep(sweep_configuration, project = "ITk_object_condensation")

# run the sweep
wandb.agent(sweep_id, function=training)

## Test

In [6]:
with open("object_condensation_default.yaml") as f:
    hparams = yaml.load(f, Loader=yaml.FullLoader)
if hparams["use_toy"]:
    hparams["regime"] = []
    hparams["spatial_channels"] = 2

model = DualHierarchicalGNN(hparams)
model_path = "/global/cfs/cdirs/m3443/usr/ryanliu/ITk_object_condensation/ITk_object_condensation/35hqbeqj/checkpoints/last.ckpt"
model = load_from_pretrained(model, model_path)
model.setup("test")

In [7]:
trainer = Trainer(gpus=1)
test_results = trainer.test(model, model.test_dataloader())

/global/homes/r/ryanliu/.conda/envs/rapids/lib/python3.8/site-packages/pytorch_lightning/loops/utilities.py:91: PossibleUserWarning: `max_epochs` was not set. Setting it to 1000 epochs. To train without an epoch limit, set `max_epochs=-1`.
  rank_zero_warn(
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
/global/homes/r/ryanliu/.conda/envs/rapids/lib/python3.8/site-packages/torch_geometric/deprecation.py:12: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: 0it [00:00, ?it/s]

Label prop iterations: 20
Label prop iterations: 6
Label prop iterations: 3
Label prop iterations: 3
Iterations: 4
77120,205,137,29,295,1371
Label prop iterations: 5
Label prop iterations: 5
Label prop iterations: 4
Iterations: 3
994,126,108,15,196,626
Label prop iterations: 2
Iterations: 1
626,63,51,8,68,125


/global/homes/r/ryanliu/.conda/envs/rapids/lib/python3.8/site-packages/pytorch_lightning/utilities/data.py:72: UserWarning: Trying to infer the `batch_size` from an ambiguous collection. The batch size we found is 2820. To avoid any miscalculations, use `self.log(..., batch_size=batch_size)`.
  warning_cache.warn(
/global/homes/r/ryanliu/.conda/envs/rapids/lib/python3.8/site-packages/cudf/core/indexed_frame.py:2271: FutureWarning: append is deprecated and will be removed in a future version. Use concat instead.
  warnings.warn(


Label prop iterations: 14
Label prop iterations: 6
Label prop iterations: 3
Label prop iterations: 2
Iterations: 4
820,191,135,25,295,1236
Label prop iterations: 5
Label prop iterations: 4
Label prop iterations: 5
Iterations: 3
621,141,118,17,210,720
Label prop iterations: 2
Iterations: 1
619,71,50,8,71,141


...

Label prop iterations: 15
Label prop iterations: 6
Label prop iterations: 4
Iterations: 3
762,131,104,15,177,979
Label prop iterations: 6
Label prop iterations: 3
Label prop iterations: 5
Label prop iterations: 3
Iterations: 4
559,147,141,12,221,729
Label prop iterations: 2
Iterations: 1
555,57,47,5,60,113
Label prop iterations: 14
Label prop iterations: 5
Label prop iterations: 3
Iterations: 3
1153,137,104,16,188,888
Label prop iterations: 5
Label prop iterations: 5
Label prop iterations: 5
Label prop iterations: 2
Iterations: 4
565,147,138,13,221,728
Label prop iterations: 2
Iterations: 1
552,59,47,6,56,111


/global/homes/r/ryanliu/.conda/envs/rapids/lib/python3.8/site-packages/pytorch_lightning/utilities/data.py:72: UserWarning: Trying to infer the `batch_size` from an ambiguous collection. The batch size we found is 2883. To avoid any miscalculations, use `self.log(..., batch_size=batch_size)`.
  warning_cache.warn(


Label prop iterations: 14
Label prop iterations: 8
Label prop iterations: 3
Iterations: 3
775,132,104,15,191,988
Label prop iterations: 5
Label prop iterations: 5
Label prop iterations: 4
Iterations: 3
561,115,107,11,163,584
Label prop iterations: 2
Iterations: 1
552,59,46,6,57,112
Label prop iterations: 14
Label prop iterations: 6
Label prop iterations: 3
Label prop iterations: 2
Iterations: 4
784,163,129,20,241,1030
Label prop iterations: 6
Label prop iterations: 8
Label prop iterations: 3
Iterations: 3
790,125,103,12,182,715
Label prop iterations: 2
Iterations: 1
777,66,48,6,65,123


/global/homes/r/ryanliu/.conda/envs/rapids/lib/python3.8/site-packages/pytorch_lightning/utilities/data.py:72: UserWarning: Trying to infer the `batch_size` from an ambiguous collection. The batch size we found is 2887. To avoid any miscalculations, use `self.log(..., batch_size=batch_size)`.
  warning_cache.warn(


Label prop iterations: 14
Label prop iterations: 6
Label prop iterations: 4
Label prop iterations: 2
Iterations: 4
794,162,129,18,231,1062
Label prop iterations: 6
Label prop iterations: 5
Label prop iterations: 4
Iterations: 3
561,115,105,9,164,616
Label prop iterations: 2
Iterations: 1
562,59,48,6,59,118
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
     assignment_loss       0.028480233624577522
        clusters            242.59019470214844
     embedding_loss        0.032324086874723434
        fake_rate          0.013966877944767475
      particle_eff          0.9178751707077026
     regression_loss        0.22951456904411316
        track_eff           0.9780920743942261
        track_pur           0.9807568192481995
        val_loss          

In [8]:
print(test_results)

[{'clusters': 242.59019470214844, 'embedding_loss': 0.032324086874723434, 'assignment_loss': 0.028480233624577522, 'regression_loss': 0.22951456904411316, 'particle_eff': 0.9178751707077026, 'track_eff': 0.9780920743942261, 'track_pur': 0.9807568192481995, 'fake_rate': 0.013966877944767475, 'val_loss': 0.03467277064919472}]
